# NJTransit Fare Zone Equity Study

In [1]:
import fiona
import pandas as pd
import geopandas as gpd
import requests
import pickle

In [2]:
import os
from dotenv import load_dotenv

load_dotenv()

api_key = os.getenv('CENSUS_API_KEY')
print(api_key)

494f201c0638a5f1c615209eedee3711d608203d


# Census Data

In [3]:
### TODO rewrite the fetcher as a function, and start with a check if the file exists locally and then load it.

In [4]:
nj_tract_table_picklefile_path = 'data/nj_tract_table_pickle.pkl'

In [5]:
#specify the data source by year and survey
year = '2022'
dsource = 'acs' #American Community Survey
dname = 'acs5' #5 year average from American Community Survey
base_url = f'https://api.census.gov/data/{year}/{dsource}/{dname}'


### TODO figure out which columns to get, median HHinc, percent non-white

In [6]:
# this request
cols = 'NAME,B28002_001E,B28002_007E' #NAME of geography as well as the variables I want to pull

In [7]:
# create picklefile nj_tract_table

def make_nj_tract_table():

    # load fips codes and iterate over counties to build up statewide dataframe
    fips_list = pd.read_csv("data/nj_county_fips.csv", dtype=object)

    county_dfs = []

    for index,county in fips_list.iterrows():

        geo = 'tract' #county geography level
        state = f'state:{county.fips_state}' 
        county = f'county:{county.fips_county}' 

        #add unique request features to the base_url
        data_url = f'{base_url}?get={cols}&for={geo}&in={state}&in={county}&key={api_key}'


        #go get the data + make df
        response = requests.get(data_url)
        data = response.json()

        df = (pd.DataFrame(data = data[1:], columns = data[0]) #first row is column names, everything else is data.
                .rename(columns = {'NAME' : 'tract_name',
                                   'B28002_001E' : 'population',
                                   'B28002_007E': 'pop_int_access',
                                   'state' : 'state_fips',
                                   'county' : 'county_fips',
                                   'tract' : 'tract_fips'}))

        #the fips for a tract is a concatenation of state, county, and tract fips
        df['fips'] = df['state_fips'] + df['county_fips'] + df['tract_fips'] #make sure these are strings so it concatenates and doesn't add. 

        #changing the data to be numeric, since everything starts as string
        df[['population', 'pop_int_access']] = df[['population', 'pop_int_access']].apply(pd.to_numeric)

        print(f"Fetched {df.size} tracts for {county}")
        county_dfs.append(df)

    # combine
    return pd.concat(county_dfs)



In [8]:
# load or create the nj_tract_table statewide tract-level demographics

# If the file exists, load the DataFrame
if os.path.exists(nj_tract_table_picklefile_path ):

    with open(nj_tract_table_picklefile_path , 'rb') as file:
        nj_tract_table = pickle.load(file)
        print(f"Loaded {nj_tract_table.size} tracts.")

# Else fetch the data and pickle it
else:
    print(f"The file '{nj_tract_table_picklefile_path}' does not exist. Fetching data")
    nj_tract_table = make_nj_tract_table()
    with open(nj_tract_table_picklefile_path, 'wb') as file:
        pickle.dump(nj_tract_table, file)
    



The file 'data/nj_tract_table_pickle.pkl' does not exist. Fetching data
Fetched 518 tracts for county:001
Fetched 1421 tracts for county:003
Fetched 819 tracts for county:005
Fetched 903 tracts for county:007
Fetched 231 tracts for county:009
Fetched 294 tracts for county:011
Fetched 1477 tracts for county:013
Fetched 483 tracts for county:015
Fetched 1281 tracts for county:017
Fetched 210 tracts for county:019
Fetched 588 tracts for county:021
Fetched 1344 tracts for county:023
Fetched 1085 tracts for county:025
Fetched 770 tracts for county:027
Fetched 1015 tracts for county:029
Fetched 840 tracts for county:031
Fetched 175 tracts for county:033
Fetched 518 tracts for county:035
Fetched 294 tracts for county:037
Fetched 840 tracts for county:039
Fetched 161 tracts for county:041


In [9]:
nj_tract_table.head()

tract_name  population  pop_int_access  \
0  Census Tract 1; Atlantic County; New Jersey         884             644   
1  Census Tract 2; Atlantic County; New Jersey        1399             935   
2  Census Tract 3; Atlantic County; New Jersey        1384             932   
3  Census Tract 4; Atlantic County; New Jersey        1696             864   
4  Census Tract 5; Atlantic County; New Jersey        1003             687   

  state_fips county_fips tract_fips         fips  
0         34         001     000100  34001000100  
1         34         001     000200  34001000200  
2         34         001     000300  34001000300  
3         34         001     000400  34001000400  
4         34         001     000500  34001000500

In [10]:
# join it to the tract base map
nj_tract_shp = gpd.read_file("./data/cb_2022_34_tract_500k/cb_2022_34_tract_500k.shp")

In [11]:
# check crsnj_tract_shp.crs

In [12]:
#tract fips is in our shape file already as GEOID
nj_map = (nj_tract_shp.merge(nj_tract_table, how = 'left', left_on = 'GEOID', right_on = 'fips')
#                     .rename(columns = {'tract_name' : 'Tract Number',
#                                        'percent_int' : 'Home Internet Access (%)',
#                                        'population' : 'Tract Population'})
         )


In [13]:
# compute area + pop density
# after https://www.educative.io/answers/how-to-plot-world-population-density-using-geopandas
nj_map['area']=nj_map.to_crs(6933).area.astype(float)*0.000001
nj_map['population_density'] = (nj_map['population'].div(nj_map['area']))

In [14]:
# # calculate pop density
# world_pop['area']=world_pop.to_crs(6933).area.astype(float)*0.000001
# world_pop['density'] = (world_pop['POP2005'].div(world_pop['area']))

#tracts are pretty small in the map, so I've opted against the black boundary outlines
nj_map.explore(
    column = 'population_density',
    tooltip = ['tract_name', 'population_density'],
    tiles = 'CartoDB positron', #fades into the background better than the default,
    scheme = 'NaturalBreaks',
    style_kwds=dict(stroke='gray', weight=0.5)
)

In [15]:
break

SyntaxError: 'break' outside loop (668683560.py, line 1)

# Bus Data

In [ ]:
gdb = "./data/njt_fare_zones.gdb"

In [ ]:
fiona.listlayers(gdb)

In [ ]:
# make a dict of geodataframes, one item per layer in the gdb

layers = dict()
for layer in fiona.listlayers(gdb):
    layers[layer] = gpd.read_file(gdb, layer=layer)

In [ ]:
layers['BUS_NJT_23Nov'].plot()

In [ ]:
layers['Pattern_Stop23Nov'].plot()